In [2]:
import pandas as pd
import json
import time
from datetime import datetime
import sqlite3

In [3]:
def apply_date(x):
    month_day = datetime.strptime(x, '%m-%d').date()
    
    # Set the year to 2023 and create the final datetime object
    return datetime(2023, month_day.month, month_day.day)

def apply_time(x):
    ampm, time =x.split(' ')
    hour, minute = map(int, time.split(':'))
    if ampm == '오후':
        hour += 12
        if hour == 24:
            hour = 0
    now = datetime.now()
    
    # Create the datetime object with the adjusted hour and minute
    return now.replace(hour=hour, minute=minute, second=0, microsecond=0)

def apply_price(x):
    try:
        return int(x.replace(',','')) 
    except:
        return None

def apply_flight_time(x):
    try:
        hour_str, minute_str = x.split()
        hours = int(hour_str.strip('시간'))
        minutes = int(minute_str.strip('분'))
        return hours * 60 + minutes  
    except:
        try:
            hour_str, minute_str = x.split(':')
            hours = int(hour_str)
            minutes = int(minute_str)
            return hours * 60 + minutes
        except:
            
            return None

In [4]:
## rar 크롤링 csv데이터 정리 및 병합 

df1 = pd.read_csv('KRtoLA.csv')
df2 = pd.read_csv('LAtoKR.csv')
df3 = pd.read_csv('hotels_7.csv')
df4 = pd.read_csv('hotels_8.csv')
df5 = pd.read_csv('hotels_9.csv')

ndf1 = df1.copy()
ndf1['departuredate'] = ndf1['departuredate'].apply(apply_date)
ndf1['arrivaldate'] = ndf1['arrivaldate'].apply(apply_date)
ndf1['departuretime'] = ndf1['departuretime'].apply(apply_time)
ndf1['arrivaltime'] = ndf1['arrivaltime'].apply(apply_time)
ndf1['price'] = ndf1['price'].apply(apply_price)
ndf1['flighttime'] = ndf1['flighttime'].apply(apply_flight_time)

ndf2 = df2.copy()

ndf2['departure_date'] = ndf2['departure_date'].apply(apply_date)
ndf2['arrival_date'] = ndf2['arrival_date'].apply(apply_date)
ndf2['departure_time'] = ndf2['departure_time'].apply(apply_time)
ndf2['arrival_time'] = ndf2['arrival_time'].apply(apply_time)
ndf2['price'] = ndf2['price'].apply(apply_price)
ndf2['flight_time'] = ndf2['flight_time'].apply(apply_flight_time)

ndf1.dropna(inplace=True)
ndf2.dropna(inplace=True)

new_lst1 = []
new_lst2 = []
for i in ndf1.index:
    depart_date = ndf1['departuredate'][i]
    arrival_date = ndf1['arrivaldate'][i]
    dy = depart_date.year
    dmon = depart_date.month
    dd = depart_date.day
    ay = arrival_date.year
    amon = arrival_date.month
    ad = arrival_date.day
    dh = ndf1['departuretime'][i].hour
    dmin = ndf1['departuretime'][i].minute
    ds = ndf1['departuretime'][i].second
    ah = ndf1['arrivaltime'][i].hour
    amin = ndf1['arrivaltime'][i].minute
    aas = ndf1['arrivaltime'][i].second
    new_lst1.append(datetime(dy,dmon,dd,dh,dmin,ds))
    new_lst2.append(datetime(ay,amon,ad,ah,amin,aas))
ndf1['departuretime'] = new_lst1
ndf1['arrivaltime'] = new_lst2

new_lst1 = []
new_lst2 = []
for i in ndf2.index:
    depart_date = ndf2['departure_date'][i]
    arrival_date = ndf2['arrival_date'][i]
    dy = depart_date.year
    dmon = depart_date.month
    dd = depart_date.day
    ay = arrival_date.year
    amon = arrival_date.month
    ad = arrival_date.day
    dh = ndf2['departure_time'][i].hour
    dmin = ndf2['departure_time'][i].minute
    ds = ndf2['departure_time'][i].second
    ah = ndf2['arrival_time'][i].hour
    amin = ndf2['arrival_time'][i].minute
    aas = ndf2['arrival_time'][i].second
    new_lst1.append(datetime(dy,dmon,dd,dh,dmin,ds))
    new_lst2.append(datetime(ay,amon,ad,ah,amin,aas))
ndf2['departure_time'] = new_lst1
ndf2['arrival_time'] = new_lst2

ndf1['departuredate'] = ndf1['departuredate'].dt.strftime('%Y-%m-%d %H:%M:%S')
ndf1['departuretime'] = ndf1['departuretime'].dt.strftime('%Y-%m-%d %H:%M:%S')
ndf1['arrivaldate'] = ndf1['arrivaldate'].dt.strftime('%Y-%m-%d %H:%M:%S')
ndf1['arrivaltime'] = ndf1['arrivaltime'].dt.strftime('%Y-%m-%d %H:%M:%S')

ndf2['departure_date'] = ndf2['departure_date'].dt.strftime('%Y-%m-%d %H:%M:%S')
ndf2['departure_time'] = ndf2['departure_time'].dt.strftime('%Y-%m-%d %H:%M:%S')
ndf2['arrival_date'] = ndf2['arrival_date'].dt.strftime('%Y-%m-%d %H:%M:%S')
ndf2['arrival_time'] = ndf2['arrival_time'].dt.strftime('%Y-%m-%d %H:%M:%S')

ndf1['flighttime'] = ndf1['flighttime'].astype(int,copy=False)
ndf1['price'] = ndf1['price'].astype(int,copy=False)
####################################################################
ndf3 = df3.copy()
ndf4 = df4.copy()
ndf5 = df5.copy()

new_col = {'departuredate':'departure_date',
           'departureday':'departure_day',
           'departuretime':'departure_time',
           'arrivaldate':'arrival_date',
           'arrivalday':'arrival_day',
           'arrivaltime':'arrival_time',
           'flighttype':'flight_type',
           'flighttime':'flight_time',
           'portd':'port_d',
           'porta':'port_a'
           }
ndf1.rename(columns=new_col,inplace=True)
ndf2.drop('Unnamed: 0',inplace = True,axis=1)
# ndf1.info()
# ndf2.info()

flight_df = pd.concat([ndf1,ndf2])
flight_df.reset_index(inplace=True)
flight_df.drop('index',axis=1,inplace=True)
flight_df.info()

hotel_df = pd.concat([ndf3,ndf4,ndf5])
hotel_df.reset_index(inplace=True)
hotel_df.drop('index',axis=1,inplace=True)
hotel_df.info()

## 정리된 데이터 csv로 저장
pd.DataFrame.to_csv(flight_df,'flights.csv')
pd.DataFrame.to_csv(hotel_df,'accommodation.csv')

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 44494 entries, 0 to 44493
Data columns (total 13 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   departure_date  44494 non-null  object
 1   departure_day   44494 non-null  object
 2   departure_time  44494 non-null  object
 3   class           44494 non-null  object
 4   arrival_date    44494 non-null  object
 5   arrival_day     44494 non-null  object
 6   arrival_time    44494 non-null  object
 7   flight_time     44494 non-null  int64 
 8   flight_type     44494 non-null  int64 
 9   price           44494 non-null  int64 
 10  airlines        44494 non-null  object
 11  port_d          44494 non-null  object
 12  port_a          44494 non-null  object
dtypes: int64(3), object(10)
memory usage: 4.4+ MB
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 33181 entries, 0 to 33180
Data columns (total 8 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          ------

33181

In [6]:
#### sqlite db에 데이터 저장.
conn = sqlite3.connect('Database.db')
cursor = conn.cursor()

flight_df.to_sql('flights',conn,if_exists='replace',index=True)
hotel_df.to_sql('accommodation',conn,if_exists='replace',index=True)

# Save (commit) the changes
conn.commit()

# 데이터 저장 확인
cursor.execute("SELECT * FROM accommodation")
rows = cursor.fetchall()

# Print the results
for row in rows:
    print(row)

(0, '아벤투라 호텔 (Aventura Hotel)', '코리아타운, 로스앤젤레스 (CA) ', 0.06, 7, '2023-09-01', '금', 8.5, 455134)
(1, '르네상스 로스앤젤레스 에어포트 호텔 (Renaissance Los Angeles Airport Hotel)', '로스앤젤레스 국제공항 (LAX), 로스앤젤레스 (CA) ', 12.9, 7, '2023-09-01', '금', 8.1, 460729)
(2, 'Four Points by Sheraton Los Angeles International Airport', '로스앤젤레스 국제공항 (LAX), 로스앤젤레스 (CA) ', 13.0, 7, '2023-09-01', '금', 7.2, 345226)
(3, 'USC 호텔 (USC Hotel)', '로스엔젤레스 다운타운, 로스앤젤레스 (CA) ', 2.3, 7, '2023-09-01', '금', 8.6, 345226)
(4, '호텔 MDR 마리나 델 레이 - 어 더블트리 바이 힐튼 (Hotel MDR Marina del Rey - a DoubleTree by Hilton)', '마리나 델 레이, 로스앤젤레스 (CA) ', 10.3, 7, '2023-09-01', '금', 7.7, 354831)
(5, 'The Biltmore Los Angeles', '로스엔젤레스 다운타운, 로스앤젤레스 (CA) ', 0.0, 7, '2023-09-01', '금', 8.0, 315708)
(6, '애너하임에 있는 숙소 (4성급) (4-star hotel in the Anaheim neighborhood)', '애너하임, 로스앤젤레스 (CA)', None, 7, '2023-09-01', '금', 8.0, 239245)
(7, '로우스 할리우드 호텔 (Loews Hollywood Hotel)', '헐리우드, 로스앤젤레스 (CA) ', 0.0, 7, '2023-09-01', '금', 8.5, 309309)
(8, '더 라인 호텔 (The LINE Hotel)', 

In [7]:
### sqlite.db 테이블 컬럼명 체크

table_name = 'flights'

# Execute the PRAGMA table_info command to get column information
cursor.execute(f"PRAGMA table_info({table_name})")

# Fetch all the rows returned by the query
column_info = cursor.fetchall()

# Close the connection to the database
conn.close()

# Print the column information
for column in column_info:
    column_name = column[1]
    data_type = column[2]
    is_nullable = column[3]
    is_primary_key = column[5]
    
    print(f"Column Name: {column_name}")
    print(f"Data Type: {data_type}")
    print(f"Is Nullable: {'YES' if is_nullable == 1 else 'NO'}")
    print(f"Is Primary Key: {'YES' if is_primary_key == 1 else 'NO'}")
    print()

Column Name: index
Data Type: INTEGER
Is Nullable: NO
Is Primary Key: NO

Column Name: departure_date
Data Type: TEXT
Is Nullable: NO
Is Primary Key: NO

Column Name: departure_day
Data Type: TEXT
Is Nullable: NO
Is Primary Key: NO

Column Name: departure_time
Data Type: TEXT
Is Nullable: NO
Is Primary Key: NO

Column Name: class
Data Type: TEXT
Is Nullable: NO
Is Primary Key: NO

Column Name: arrival_date
Data Type: TEXT
Is Nullable: NO
Is Primary Key: NO

Column Name: arrival_day
Data Type: TEXT
Is Nullable: NO
Is Primary Key: NO

Column Name: arrival_time
Data Type: TEXT
Is Nullable: NO
Is Primary Key: NO

Column Name: flight_time
Data Type: INTEGER
Is Nullable: NO
Is Primary Key: NO

Column Name: flight_type
Data Type: INTEGER
Is Nullable: NO
Is Primary Key: NO

Column Name: price
Data Type: INTEGER
Is Nullable: NO
Is Primary Key: NO

Column Name: airlines
Data Type: TEXT
Is Nullable: NO
Is Primary Key: NO

Column Name: port_d
Data Type: TEXT
Is Nullable: NO
Is Primary Key: NO

Col